# EV Optimal Placement Optimisation
**Prompt**

Below is the problem formulation for the EV optimal placement optimisation problem.

Objective:

$$\text{Max} \sum_{i \in B} Y_{ij} \quad \forall j \in D$$

Decision Variables:
1. **Number of Chargers (Ni)**:
$$N_i \geq P, \forall i \in B$$

2. **Coverage Radius (Ri)**:
$$R_i = k \times N_i, \forall i \in B$$

3. **Distance Constraint**:
$$R_i \leq R_{\text{max}}$$

4. **Coverage Constraints (Yij)**:
$$D_{ij} \leq R_i + 99 \times (1 - Y_{ij}), \forall i \in B, j \in D$$
$$D_{ij} \geq R_i - 99 \times Y_{ij}, \forall i \in B, j \in D$$
$$\sum_{i \in B} Y_{ij} \geq 1, \forall j \in D$$

5. **Budget Constraint**:
$$\sum_{i \in B} C \times N_i \leq W$$

Assume the role of a data engineer specialized in data and prescriptive analytics. You are proficient in constructing mathematical models and adept at programming and solving these models using the Gurobi library. In our subsequent interactions, you will be tasked with coding various optimization models utilizing the Gurobi library. Your objectives are to ensure accurate results and adhere to the following guidelines:
1. Generate random parameters when specific parameters are not provided.
2. After solving each optimization problem, verify the problem status. If the status is "OPTIMAL", include code snippets to retrieve and display the optimal solutions and the objective value.
3. Disable output logging by setting the "OutputFlag" to 0.
4. Present the results in a concise and clear format, utilizing tables or graphical representations when beneficial.
5. Strive for code efficiency, utilizing the minimal amount of code necessary for model programming.
6. If possible, use “addVars” for non-scalar decision variables and use “addConstrs” for a batch of constraints. Also, please use “quicksum” instead of “sum”.
7. Be careful of the indices given that Python starts from 0 but most of the models start from 1. 
8. Make sure the code you provided fulfills all the requirements, i.e., a complete code should be provided. 

Please define the EV Charger Placement Optimisation problem as a function with detailed comments in the code, solve the problem and retrieve the optimal solutions and objective value, and return the solution.

(Note: Of course, the GAI generated code was modified quite significantly to meet all of above's complex requirements.)

In [1]:
import gurobipy as gp
from gurobipy import GRB

In [3]:
def solve_ev_optimal_placement(B, D, P, k, R_max, C, W, D_ij):
    """
    Solve the EV Optimal Placement Optimization problem.

    Parameters:
    - B (int): Number of car parks.
    - D (int): Number of points of interest.
    - P (int): Minimum number of chargers required at each car park.
    - k (float): Constant for coverage radius calculation.
    - R_max (float): Maximum coverage radius.
    - C (float): Variable cost of installing one charging station.
    - W (float): Total budget.
    - D_ij (dict): Dictionary containing distances between car parks and points of interest.

    Returns:
    - model: Gurobi model object.
    """
    # Create a new Gurobi model
    model = gp.Model("EV_Optimal_Placement")

    # Disable output logging
    model.Params.OutputFlag = 0

    # Decision variables
    Ni = model.addVars(B, lb=P, vtype=GRB.INTEGER, name="Ni")  # Number of chargers
    Ri = model.addVars(B, name="Ri")  # Coverage radius
    Y = model.addVars(B, D, vtype=GRB.BINARY, name="Y")  # Coverage indicator

    # Objective function
    obj = gp.quicksum(Y[i, j] for i in range(B) for j in range(D))
    model.setObjective(obj, sense=GRB.MAXIMIZE)

    # Constraints
    # Number of chargers constraint
    model.addConstrs(
        (Ni[i] >= P for i in range(B)), name="charger_num_constr"
    )

    # Coverage radius constraint
    model.addConstrs(
        (Ri[i] == k * Ni[i] for i in range(B)), name="radius_constr"
    )

    # Distance constraint
    model.addConstrs(
        (Ri[i] <= R_max for i in range(B)), name="distance_constrs"
    )

    # Coverage constraints
    print("Coverage constraints:")
    for i in range(B):
        for j in range(D):
            # D_ij.get(i, {}) returns an empty dictionary if i is not in D_ij
            # .get(j, None) returns None if j is not found in the dictionary returned by D_ij.get(i, {})
            distance = D_ij.get(i, {}).get(j, None)
            print(f"Distance between car park {i} and point of interest {j}: {distance}")
            if distance is not None:
                model.addConstr(Y[i, j] * (Ri[i] + 999999 * (1 - Y[i, j])) >= distance, name=f"coverage_constrs_1_{i}_{j}")
                model.addConstr(
                    Y[i, j] * (Ri[i] - 999999 * Y[i, j]) <= distance,
                    name=f"coverage_constrs_2_{i}_{j}",
                )

    for j in range(D):
        model.addConstr(gp.quicksum(Y[i, j] for i in range(B)) >= 1, name=f"coverage_constrs_3_{j}")

    # Budget constraint
    model.addConstr(
        (gp.quicksum(C * Ni[i] for i in range(B)) <= W), name="budget_constr"
    )

    # Optimize the model
    model.optimize()

    # Verify problem status
    if model.status == GRB.OPTIMAL:
        # Retrieve and display optimal solutions
        # Charger placement at each car park
        print("Charger Placement Results:")
        for i in range(B):
            print(f"Carpark {i}: Number of chargers = {Ni[i].x:.0f}, Coverage radius = {Ri[i].x:.2f} km")

        # Points of interest coverage
        print("\nPoints of Interest Coverage:")
        for j in range(D):
            covered = any(Y[i, j].x for i in range(B))
            print(f"Point of interest {j}: {'Covered' if covered else 'Not Covered'}")

        # Display objective value
        print(f"Total coverage: {model.objVal:.2f}")
        print(f"Proportion of points of interest covered: {model.objVal / D:.2f}")
    else:
        print("No optimal solution found.")
        return None

    # Return the model and solution
    return model, model.objVal

## Calculate Distance Matrix
**Prompt**

I have 2 prepared datasets.
1. Carparks, with name, latitude, longtitude and type - this has 1273 carparks
2. Points of interest, with name, latitude, longtitude and type - this has 13032 POIs

Construct a D_ij matrix using the haversine formula. To improve time and space complexity, I only want to store distances that are 1000 meters (1km) or less. Store the results in a pickle file.

In [5]:
from math import radians, sin, cos, sqrt, atan2
import pickle
import pandas as pd

def haversine_distance(lat1, lon1, lat2, lon2):
    # Convert latitude and longitude from degrees to radians
    lat1, lon1, lat2, lon2 = map(radians, [lat1, lon1, lat2, lon2])

    # Haversine formula
    dlat = lat2 - lat1
    dlon = lon2 - lon1
    a = sin(dlat / 2) ** 2 + cos(lat1) * cos(lat2) * sin(dlon / 2) ** 2
    c = 2 * atan2(sqrt(a), sqrt(1 - a))
    distance = 6371 * c  # Radius of Earth in kilometers
    return distance * 1000  # Convert to meters

# Function to construct distance matrix and save it to a pickle file
def construct_distance_matrix(carparks_df, pois_df, filename):
    D_ij = {}

    for cp_index, carpark in carparks_df.iterrows():
        D_ij[cp_index] = {}

        for poi_index, poi in pois_df.iterrows():
            distance = haversine_distance(
                carpark["latitude"],
                carpark["longitude"],
                poi["latitude"],
                poi["longitude"],
            )
            if distance <= 1000:  # Store distances <= 1000 meters
                D_ij[cp_index][poi_index] = distance

    # Save the distance matrix to a pickle file
    with open(filename, "wb") as f:
        pickle.dump(D_ij, f)

    return D_ij


In [6]:
carparks_df = pd.read_csv("data/CombinedCarpark.csv")
pois_df = pd.read_csv("data/CombinedPOI.csv")
pkl_filename = "data/distance_matrix.pkl"

In [ ]:
D_ij = construct_distance_matrix(carparks_df, pois_df, pkl_filename)

In [9]:
print("size of outer D_ij: ", len(D_ij))
D_ij

size of outer D_ij:  1273


{0: {22: 903.3639148673276,
  65: 494.9691781542487,
  1703: 603.3065504812,
  2327: 976.0407962450982,
  2536: 960.614277658531,
  2665: 940.3079285221487,
  3539: 475.59773637262145,
  3560: 475.9207609859285,
  3580: 475.2037506820089,
  3842: 732.2975489603937,
  4024: 697.8952610493939,
  4070: 348.16008256193976,
  4088: 376.84030607809007,
  4103: 341.8001904864662,
  4114: 306.0795735255624,
  4207: 68.70586007603058,
  4214: 68.00480008515972,
  4219: 106.86637847138041,
  4223: 71.19033835313745,
  4230: 739.325684914142,
  4247: 4.315380890727901,
  4263: 20.257471311651734,
  4430: 646.77619716126,
  4439: 677.7345115105945,
  4577: 617.4627037256402,
  4759: 578.3888907719221,
  4974: 655.9130038542231,
  7469: 874.7447241273211,
  7490: 843.7847686646049,
  7497: 852.6609918579192,
  7512: 973.9297285098911,
  7530: 985.5074800028004,
  8037: 449.0754506239831,
  9830: 557.9111801932715,
  9852: 524.4120641535836,
  9875: 566.4644906361593,
  9891: 626.442739134472,
  991

## Solving the LOP

In [13]:
#SMALL-SCALE TESTING
# Parameters
B = 4
D = 5
P = 3  # Minimum number of chargers required at each car park
k = 27.17  # Constant for coverage radius calculation (in meters)
R_max = 1000  # Maximum coverage radius (in meters)
C = 10500  # Variable cost of installing one charging station
W = 630000000  # Total budget
D_ij_small = {
    0: {1: 100, 3: 200},
    1: {2: 300, 3: 400},
    2: {2: 500, 3: 600},
    3: {2: 700, 4: 800}
}

# Solve the EV Optimal Placement Optimization problem
model = solve_ev_optimal_placement(B, D, P, k, R_max, C, W, D_ij_small)

Coverage constraints:
Distance between car park 0 and point of interest 0: None
Distance between car park 0 and point of interest 1: 100
Distance between car park 0 and point of interest 2: None
Distance between car park 0 and point of interest 3: 200
Distance between car park 0 and point of interest 4: None
Distance between car park 1 and point of interest 0: None
Distance between car park 1 and point of interest 1: None
Distance between car park 1 and point of interest 2: 300
Distance between car park 1 and point of interest 3: 400
Distance between car park 1 and point of interest 4: None
Distance between car park 2 and point of interest 0: None
Distance between car park 2 and point of interest 1: None
Distance between car park 2 and point of interest 2: 500
Distance between car park 2 and point of interest 3: 600
Distance between car park 2 and point of interest 4: None
Distance between car park 3 and point of interest 0: None
Distance between car park 3 and point of interest 1: Non

In [41]:
# ACTUAL
B = len(carparks_df)  # Number of car parks
D = len(pois_df)  # Number of points of interest
P = 3  # Minimum number of chargers required at each car park
k = 27.17  # Constant for coverage radius calculation (in meters)
R_max = 500  # Maximum coverage radius (in meters)
C = 10500  # Variable cost of installing one charging station
W = 630000000  # Total budget

# Load the distance matrix from the pickle file
with open(pkl_filename, "rb") as f:
    D_ij = pickle.load(f)

# print parameters
print(
    f"Num of car parks: {B}, Num of POIs: {D}, Min num of chargers: {P}, Constant for coverage radius: {k}, Max coverage radius: {R_max}, Variable cost of installing one charging station: {C}, Total budget: {W}"
)

# Solve the EV Optimal Placement Optimization problem
model, soln = solve_ev_optimal_placement(B, D, P, k, R_max, C, W, D_ij)

Num of car parks: 1273, Num of POIs: 13032, Min num of chargers: 3, Constant for coverage radius: 27.17, Max coverage radius: 500, Variable cost of installing one charging station: 10500, Total budget: 630000000
